In [6]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torchvision
import torchvision.transforms as transforms
from torchvision.utils import save_image
from torch.autograd import Variable
import time

In [7]:
print ("Start : %s" % time.ctime())


Start : Mon Nov  2 10:32:04 2020


In [8]:
# define generator
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.fc1 = nn.Linear(100, 256)
        self.fc2 = nn.Linear(256, 256)
        self.fc3 = nn.Linear(256, 784)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.tanh(self.fc3(x))
        return x


# define descriminator
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        self.fc1 = nn.Linear(784, 256)
        self.fc2 = nn.Linear(256, 256)
        self.fc3 = nn.Linear(256, 1)

    def forward(self, x):
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = torch.sigmoid(self.fc3(x))
        return x

# transform input to [0,1] then [-1.1]
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize([0.5], [0.5]),
])

trainset = torchvision.datasets.MNIST(root='./data', train=True, download=True, transform=transform)
trainloader = torch.utils.data.DataLoader(trainset, batch_size=128, shuffle=True)

testset = torchvision.datasets.MNIST(root='./data', train=False, download=True, transform=transform)
testloader = torch.utils.data.DataLoader(testset, batch_size=100, shuffle=False)

D = Discriminator()
G = Generator()
d_optimizer = torch.optim.Adam(D.parameters(), lr=0.0003)
g_optimizer = torch.optim.Adam(G.parameters(), lr=0.0003)

criterion = nn.BCELoss()

In [9]:
# Training
def train(epoch):
    D.train()
    G.train()
    g_loss = 0.
    d_loss = 0.
    for batch_idx, (inputs, targets) in enumerate(trainloader):
        # flatten the image 
        real_imgs = torch.flatten(inputs, start_dim=1)

        # real/fake label
        real_label = Variable(torch.ones(real_imgs.size(0)))
        fake_label = Variable(torch.zeros(real_imgs.size(0)))

        # train D
        # real image loss
        real_out = D(real_imgs)
        d_loss_real = criterion(real_out, real_label)

        # generate image loss
        z = Variable(torch.randn(real_imgs.size(0), 100))
        fake_imgs = G(z)
        fake_output = D(fake_imgs)
        d_loss_fake = criterion(fake_output, fake_label)

        # update the gradiant
        d_loss = d_loss_real + d_loss_fake
        d_optimizer.zero_grad()
        d_loss.backward()
        d_optimizer.step()


        # train G
        # loss
        z = Variable(torch.randn(real_imgs.size(0), 100))
        fake_imgs = G(z)
        output = D(fake_imgs)
        g_loss = criterion(output, real_label)

        # update gradiant
        g_optimizer.zero_grad()
        g_loss.backward()
        g_optimizer.step()


        g_loss = g_loss.item()
        d_loss = d_loss.item()
        print('Epoch {},Batch {}, g_loss: {:.6f}, d_loss: {:.6f}'.format(epoch, batch_idx, g_loss, d_loss))

        # save image
        fake_images = fake_imgs.view(-1, 1, 28, 28)
        save_image(fake_images, '/Users/qianchenliu/Study/ML/MNIST_FAKE_GAN/fake_images-{}.png'.format(epoch + 1))


# train 200 epochs
for epoch in range(200):
    train(epoch)

torch.save(G.state_dict(), '/Users/qianchenliu/Study/ML/gan_g.pth')
torch.save(D.state_dict(), '/Users/qianchenliu/Study/ML/gan_d.pth')


Epoch 0,Batch 0, g_loss: 0.709254, d_loss: 1.370663
Epoch 0,Batch 1, g_loss: 0.703871, d_loss: 1.232131
Epoch 0,Batch 2, g_loss: 0.699633, d_loss: 1.112020
Epoch 0,Batch 3, g_loss: 0.692982, d_loss: 1.015957
Epoch 0,Batch 4, g_loss: 0.686579, d_loss: 0.939186
Epoch 0,Batch 5, g_loss: 0.677607, d_loss: 0.876792
Epoch 0,Batch 6, g_loss: 0.666377, d_loss: 0.833774
Epoch 0,Batch 7, g_loss: 0.652533, d_loss: 0.810470
Epoch 0,Batch 8, g_loss: 0.635402, d_loss: 0.805678
Epoch 0,Batch 9, g_loss: 0.623300, d_loss: 0.812416
Epoch 0,Batch 10, g_loss: 0.601578, d_loss: 0.825620
Epoch 0,Batch 11, g_loss: 0.588297, d_loss: 0.849622
Epoch 0,Batch 12, g_loss: 0.570950, d_loss: 0.879962
Epoch 0,Batch 13, g_loss: 0.559594, d_loss: 0.901690
Epoch 0,Batch 14, g_loss: 0.551252, d_loss: 0.928424
Epoch 0,Batch 15, g_loss: 0.547764, d_loss: 0.941912
Epoch 0,Batch 16, g_loss: 0.553245, d_loss: 0.955002
Epoch 0,Batch 17, g_loss: 0.564460, d_loss: 0.957641
Epoch 0,Batch 18, g_loss: 0.590420, d_loss: 0.936749
Epo

Epoch 0,Batch 156, g_loss: 1.920919, d_loss: 0.212710
Epoch 0,Batch 157, g_loss: 1.690230, d_loss: 0.290804
Epoch 0,Batch 158, g_loss: 1.462132, d_loss: 0.358065
Epoch 0,Batch 159, g_loss: 1.328660, d_loss: 0.440827
Epoch 0,Batch 160, g_loss: 1.169654, d_loss: 0.529952
Epoch 0,Batch 161, g_loss: 1.096360, d_loss: 0.611097
Epoch 0,Batch 162, g_loss: 1.058734, d_loss: 0.608969
Epoch 0,Batch 163, g_loss: 1.118022, d_loss: 0.563631
Epoch 0,Batch 164, g_loss: 1.238334, d_loss: 0.502861
Epoch 0,Batch 165, g_loss: 1.380313, d_loss: 0.434108
Epoch 0,Batch 166, g_loss: 1.604089, d_loss: 0.372222
Epoch 0,Batch 167, g_loss: 1.791694, d_loss: 0.307249
Epoch 0,Batch 168, g_loss: 2.000678, d_loss: 0.254303
Epoch 0,Batch 169, g_loss: 2.208933, d_loss: 0.207998
Epoch 0,Batch 170, g_loss: 2.312908, d_loss: 0.198492
Epoch 0,Batch 171, g_loss: 2.380031, d_loss: 0.163223
Epoch 0,Batch 172, g_loss: 2.450425, d_loss: 0.145750
Epoch 0,Batch 173, g_loss: 2.467354, d_loss: 0.139727
Epoch 0,Batch 174, g_loss: 2

Epoch 0,Batch 311, g_loss: 3.366309, d_loss: 0.242589
Epoch 0,Batch 312, g_loss: 3.378740, d_loss: 0.328323
Epoch 0,Batch 313, g_loss: 3.335006, d_loss: 0.355095
Epoch 0,Batch 314, g_loss: 1.300364, d_loss: 0.785896
Epoch 0,Batch 315, g_loss: 1.383109, d_loss: 1.292278
Epoch 0,Batch 316, g_loss: 2.649488, d_loss: 1.160273
Epoch 0,Batch 317, g_loss: 2.799876, d_loss: 0.983509
Epoch 0,Batch 318, g_loss: 1.657206, d_loss: 1.234774
Epoch 0,Batch 319, g_loss: 1.428584, d_loss: 1.039705
Epoch 0,Batch 320, g_loss: 2.042601, d_loss: 1.134914
Epoch 0,Batch 321, g_loss: 3.298542, d_loss: 0.612678
Epoch 0,Batch 322, g_loss: 4.057514, d_loss: 0.470689
Epoch 0,Batch 323, g_loss: 4.322427, d_loss: 0.323134
Epoch 0,Batch 324, g_loss: 4.583189, d_loss: 0.093046
Epoch 0,Batch 325, g_loss: 4.627809, d_loss: 0.061039
Epoch 0,Batch 326, g_loss: 4.525196, d_loss: 0.027447
Epoch 0,Batch 327, g_loss: 4.381834, d_loss: 0.027507
Epoch 0,Batch 328, g_loss: 4.251164, d_loss: 0.035721
Epoch 0,Batch 329, g_loss: 3

Epoch 0,Batch 463, g_loss: 3.657702, d_loss: 0.177339
Epoch 0,Batch 464, g_loss: 3.576783, d_loss: 0.195934
Epoch 0,Batch 465, g_loss: 3.388263, d_loss: 0.246407
Epoch 0,Batch 466, g_loss: 3.266670, d_loss: 0.314851
Epoch 0,Batch 467, g_loss: 3.101096, d_loss: 0.427091
Epoch 0,Batch 468, g_loss: 3.546995, d_loss: 0.473522


/Users/qianchenliu/opt/anaconda3/lib/python3.8/site-packages/torch/nn/modules/loss.py:529: UserWarning: Using a target size (torch.Size([96])) that is different to the input size (torch.Size([96, 1])) is deprecated. Please ensure they have the same size.
  return F.binary_cross_entropy(input, target, weight=self.weight, reduction=self.reduction)


...

Epoch 198,Batch 204, g_loss: 0.981356, d_loss: 1.166246
Epoch 198,Batch 205, g_loss: 0.963358, d_loss: 1.215219
Epoch 198,Batch 206, g_loss: 1.111366, d_loss: 1.182818
Epoch 198,Batch 207, g_loss: 1.164536, d_loss: 1.193445
Epoch 198,Batch 208, g_loss: 1.222420, d_loss: 1.112068
Epoch 198,Batch 209, g_loss: 1.176098, d_loss: 1.077522
Epoch 198,Batch 210, g_loss: 1.347489, d_loss: 1.160211
Epoch 198,Batch 211, g_loss: 1.293339, d_loss: 1.152504
Epoch 198,Batch 212, g_loss: 1.041148, d_loss: 1.186588
Epoch 198,Batch 213, g_loss: 1.039808, d_loss: 1.088531
Epoch 198,Batch 214, g_loss: 1.071947, d_loss: 1.025531
Epoch 198,Batch 215, g_loss: 1.000149, d_loss: 1.037914
Epoch 198,Batch 216, g_loss: 1.127444, d_loss: 1.140004
Epoch 198,Batch 217, g_loss: 1.237698, d_loss: 1.032980
Epoch 198,Batch 218, g_loss: 1.305692, d_loss: 0.987731
Epoch 198,Batch 219, g_loss: 1.348701, d_loss: 1.161870
Epoch 198,Batch 220, g_loss: 1.267613, d_loss: 1.138571
Epoch 198,Batch 221, g_loss: 1.277091, d_loss: 1

Epoch 198,Batch 353, g_loss: 1.358971, d_loss: 1.025765
Epoch 198,Batch 354, g_loss: 1.278773, d_loss: 1.028449
Epoch 198,Batch 355, g_loss: 1.327652, d_loss: 1.042669
Epoch 198,Batch 356, g_loss: 1.260996, d_loss: 0.915920
Epoch 198,Batch 357, g_loss: 1.246321, d_loss: 1.179075
Epoch 198,Batch 358, g_loss: 1.353618, d_loss: 1.065771
Epoch 198,Batch 359, g_loss: 1.326068, d_loss: 1.076504
Epoch 198,Batch 360, g_loss: 1.187731, d_loss: 1.051523
Epoch 198,Batch 361, g_loss: 1.311179, d_loss: 1.151055
Epoch 198,Batch 362, g_loss: 1.231907, d_loss: 1.256046
Epoch 198,Batch 363, g_loss: 1.092038, d_loss: 1.094417
Epoch 198,Batch 364, g_loss: 1.155226, d_loss: 1.207848
Epoch 198,Batch 365, g_loss: 1.174402, d_loss: 1.127091
Epoch 198,Batch 366, g_loss: 1.224649, d_loss: 1.135104
Epoch 198,Batch 367, g_loss: 1.193402, d_loss: 1.341307
Epoch 198,Batch 368, g_loss: 1.200776, d_loss: 1.208283
Epoch 198,Batch 369, g_loss: 1.243340, d_loss: 1.108878
Epoch 198,Batch 370, g_loss: 1.073622, d_loss: 1

Epoch 199,Batch 33, g_loss: 1.178283, d_loss: 1.131491
Epoch 199,Batch 34, g_loss: 0.980229, d_loss: 1.075354
Epoch 199,Batch 35, g_loss: 0.991890, d_loss: 1.127520
Epoch 199,Batch 36, g_loss: 1.022114, d_loss: 1.127544
Epoch 199,Batch 37, g_loss: 1.189615, d_loss: 1.055258
Epoch 199,Batch 38, g_loss: 1.195414, d_loss: 1.051007
Epoch 199,Batch 39, g_loss: 1.288363, d_loss: 1.028764
Epoch 199,Batch 40, g_loss: 1.272736, d_loss: 1.014116
Epoch 199,Batch 41, g_loss: 1.342099, d_loss: 1.122671
Epoch 199,Batch 42, g_loss: 1.300931, d_loss: 0.952994
Epoch 199,Batch 43, g_loss: 1.227200, d_loss: 1.012620
Epoch 199,Batch 44, g_loss: 1.368663, d_loss: 0.881070
Epoch 199,Batch 45, g_loss: 1.264770, d_loss: 1.000583
Epoch 199,Batch 46, g_loss: 1.299224, d_loss: 0.987028
Epoch 199,Batch 47, g_loss: 1.323206, d_loss: 0.991262
Epoch 199,Batch 48, g_loss: 1.140500, d_loss: 1.007271
Epoch 199,Batch 49, g_loss: 1.217869, d_loss: 0.964702
Epoch 199,Batch 50, g_loss: 1.404579, d_loss: 0.944550
Epoch 199,

Epoch 199,Batch 182, g_loss: 1.249098, d_loss: 1.035007
Epoch 199,Batch 183, g_loss: 1.332707, d_loss: 1.000344
Epoch 199,Batch 184, g_loss: 1.334458, d_loss: 0.969954
Epoch 199,Batch 185, g_loss: 1.651737, d_loss: 0.891410
Epoch 199,Batch 186, g_loss: 1.672067, d_loss: 0.968873
Epoch 199,Batch 187, g_loss: 1.727839, d_loss: 0.831065
Epoch 199,Batch 188, g_loss: 1.653143, d_loss: 0.970259
Epoch 199,Batch 189, g_loss: 1.385483, d_loss: 0.974324
Epoch 199,Batch 190, g_loss: 1.309584, d_loss: 0.982364
Epoch 199,Batch 191, g_loss: 1.316299, d_loss: 0.924739
Epoch 199,Batch 192, g_loss: 1.244540, d_loss: 0.903902
Epoch 199,Batch 193, g_loss: 1.383961, d_loss: 0.937815
Epoch 199,Batch 194, g_loss: 1.295839, d_loss: 0.930754
Epoch 199,Batch 195, g_loss: 1.315347, d_loss: 0.962771
Epoch 199,Batch 196, g_loss: 1.411767, d_loss: 1.017694
Epoch 199,Batch 197, g_loss: 1.329690, d_loss: 0.971149
Epoch 199,Batch 198, g_loss: 1.533712, d_loss: 0.917136
Epoch 199,Batch 199, g_loss: 1.430004, d_loss: 1

Epoch 199,Batch 330, g_loss: 1.398860, d_loss: 0.980205
Epoch 199,Batch 331, g_loss: 1.379213, d_loss: 0.978499
Epoch 199,Batch 332, g_loss: 1.422161, d_loss: 0.863881
Epoch 199,Batch 333, g_loss: 1.589361, d_loss: 0.876784
Epoch 199,Batch 334, g_loss: 1.456547, d_loss: 0.927176
Epoch 199,Batch 335, g_loss: 1.511169, d_loss: 0.909811
Epoch 199,Batch 336, g_loss: 1.473648, d_loss: 0.917719
Epoch 199,Batch 337, g_loss: 1.334100, d_loss: 0.919778
Epoch 199,Batch 338, g_loss: 1.472077, d_loss: 1.031277
Epoch 199,Batch 339, g_loss: 1.233581, d_loss: 0.972077
Epoch 199,Batch 340, g_loss: 1.345872, d_loss: 1.082124
Epoch 199,Batch 341, g_loss: 1.280384, d_loss: 1.107700
Epoch 199,Batch 342, g_loss: 1.261589, d_loss: 1.041604
Epoch 199,Batch 343, g_loss: 1.349170, d_loss: 1.044285
Epoch 199,Batch 344, g_loss: 1.338255, d_loss: 1.004550
Epoch 199,Batch 345, g_loss: 1.191362, d_loss: 1.146312
Epoch 199,Batch 346, g_loss: 1.148233, d_loss: 1.047248
Epoch 199,Batch 347, g_loss: 1.235429, d_loss: 1

In [10]:
print ("End : %s" % time.ctime())

End : Mon Nov  2 12:48:36 2020
